<a href="https://colab.research.google.com/github/dhirajsah26/EmbeddingWord2Vec/blob/main/EMBEDDING__WORD2VEC.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Assignment_1 Section_2
Darshan Ruparel
Dhiraj Kumar Sah
Dhru Prajapati
Nisarg  Patel


In [1]:
import pandas as pd
import numpy as np
import re

import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize
import string

from gensim.models import Word2Vec
from nltk.tokenize import word_tokenize
import logging

from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.layers import Embedding, LSTM, Dense
from tensorflow.keras.models import Sequential
from tensorflow.keras.utils import to_categorical


In [2]:
df = pd.read_csv('/content/drive/MyDrive/Data/datset_54665.csv')

In [3]:
df.shape

(10933, 6)

In [4]:
# dorpna and reset index

df.dropna(inplace=True)
df.reset_index(drop=True, inplace=True)


In [5]:
df.shape

(6794, 6)

In [6]:
df.sample(5)

Unnamed: 0                                      question_name  \
2071        3291     How to stop constipation and pain in the back?   
4531        7444  Why is there tightness and pain below my ribs ...   
2731        4418                   Why are my liver enzymes raised?   
2813        4558  I have belly discomfort and pain due to ulcera...   
1935        3126  Can ADHD make an 8-year-old angry at home and ...   

                                   question_description  \
2071  Hello doctor,\nI have been suffering from bout...   
4531  Hello doctor,\r\nThere is a tight feeling belo...   
2731  Hello doctor,\nToday I took blood test and fou...   
2813  Hi doctor,\r\nI have had ulcerative colitis si...   
1935  Hello doctor,My son is 8 years old. In school,...   

                                            answer_text  \
2071  Hello,\nWelcome to icliniq.com.\nI went throug...   
4531  Hi,\r\nWelcome to icliniq.com.\r\nI have gone ...   
2731  Hello,\n\nWelcome to icliniq.com. According to...   
2813  Hi,\r\nWelcome to icliniq.com.\r\nWell, since ...   
1935  Hello,\r\nWelcome to icliniq.com.\r\nYes, your...   

                        source              value  
2071              Rheumatology          Back Pain  
4531         Internal Medicine   Chest Discomfort  
2731  Medical Gastroenterology        Fatty Liver  
2813  Medical Gastroenterology               Sibo  
1935                Psychiatry  Behavior Disorder

In [7]:
columns = ['question_name', 'question_description','answer_text','source','value']

In [8]:
df = df[columns]

In [9]:
df.sample(5)

question_name  \
6246           Please explain the presentation of DVT.    
685   How to reduce fat in my belly without looking ...   
2023  Whom should I opt for diagnosing ADHD in a 12-...   
3009  What are the possible options available to tre...   
22    Can long-term use of Escitalopram cause weight...   

                                   question_description  \
6246  Hi doctor,\nI am an 18 year old healthy female...   
685   Hello doctor,\r\nI have a normal body and a hu...   
2023  Hello doctor,\nI want your opinion on who is t...   
3009  Hi doctor,\nI have been having erectile dysfun...   
22    Hello doctor,\nI have been using Escitalopram ...   

                                            answer_text            source  \
6246  Hello,\n\nWelcome to icliniq.com. DVT - deep v...         Radiology   
685   Hello, \r\nWelcome to icliniq.com. \r\nYou see...  General Medicine   
2023  Hello,\n\nWelcome to icliniq.com.\n\nYou have ...        Psychiatry   
3009  Hi,\n\nWelcome to icliniq.com.\n\nThe followin...          Sexology   
22    Hi,\nWelcome to icliniq.com.\nI read your quer...        Cardiology   

                              value  
6246           Deep Vein Thrombosis  
685                         Fasting  
2023  Methylphenidate Hydrochloride  
3009                  Poor Erection  
22                          Anxiety

In [10]:
df_preprocessing = df.copy(deep=True)

In [11]:
pattern = re.compile(r'welcome\sto\sicliniq\.com\.')

In [12]:
def remove_url(text):
    return pattern.sub('', text)

# # Apply the function to the 'question_description' column
# df['answer_text'] = df['answer_text'].apply(lambda x: remove_url(x))


In [13]:
# def clean_text(text):
#   text = text.lower()
#   text = re.sub(r"i'm", "i am", text)
#   text = re.sub(r"he's", "he is", text)

Preporocession the text

In [14]:
# Download NLTK resources
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


True

In [15]:
def preprocess_text(text):
    # Convert to lowercase
    text = text.lower()
    text = remove_url(text)
    # Remove punctuation
    text = text.translate(str.maketrans('', '', string.punctuation))
    # print(text)
    # Tokenization
    tokens = word_tokenize(text)

    # Remove stopwords
    stop_words = set(stopwords.words('english'))
    tokens = [word for word in tokens if word not in stop_words]
    # print(tokens)
    # Lemmatization
    lemmatizer = WordNetLemmatizer()
    tokens = [lemmatizer.lemmatize(word) for word in tokens]

    # Reassemble the tokens into a string
    preprocessed_text = ' '.join(tokens)

    return preprocessed_text


In [16]:
# srr ="Hi doctor, I am female, 36 years old, 5 feet, generally healthy. I have recently found a small hard pea sized painless lump on my left collar bone, it moves around and I have had for periods of few days at a time over last few months, very sore, tender to touch breasts. I have not seen anyone about this yet as it is recent and thought it would pass. Do I have to be concerned?"

In [17]:
# preprocess_text(srr)

In [18]:
# Apply text preprocessing to 'question_description' and 'answer_text' columns
df_preprocessing['question_description'] = df_preprocessing['question_description'].apply(preprocess_text)
df_preprocessing['answer_text'] = df_preprocessing['answer_text'].apply(preprocess_text)


In [19]:
# Display the preprocessed DataFrame
print(df_preprocessing.head())

                                       question_name  \
0  What could cause palpitations in chest and abd...   
1                      How can I get rid of anxiety?   
2  How can a person overcome the feeling of guilt...   
3  What causes anxiety and overthinking, along wi...   
4  Is there any way to control nervousness and fo...   

                                question_description  \
0  hi doctori 27 year old blood pressure range 11...   
1  hi doctor recently experienced choking episode...   
2  hi doctoron regular day many problem guilt sha...   
3  hello doctor feel severe anxiety overthink lot...   
4  hello doctori problem get nervous fast think l...   

                                         answer_text      source    value  
0  hello understand concern issue palpitation pal...  Cardiology  Anxiety  
1  hi thank query following thing might help anxi...  Cardiology  Anxiety  
2  hello understand concern symptom like guilt pr...  Cardiology  Anxiety  
3  hello thank query r

In [20]:
df_preprocessing

question_name  \
0     What could cause palpitations in chest and abd...   
1                         How can I get rid of anxiety?   
2     How can a person overcome the feeling of guilt...   
3     What causes anxiety and overthinking, along wi...   
4     Is there any way to control nervousness and fo...   
...                                                 ...   
6789  Kindly help me to fix the jaw pain from clench...   
6790  Does testicle surgery done to prevent their tw...   
6791  How to manage recurrent herpes infection on th...   
6792  What could be the reason for pain and discomfo...   
6793  Is surgery possible for cryptorchidism in a 25...   

                                   question_description  \
0     hi doctori 27 year old blood pressure range 11...   
1     hi doctor recently experienced choking episode...   
2     hi doctoron regular day many problem guilt sha...   
3     hello doctor feel severe anxiety overthink lot...   
4     hello doctori problem get nervous fast think l...   
...                                                 ...   
6789  hi doctor clench jaw lot mouth hurt quite bit ...   
6790  hello doctor 17yearold male need peace mind qu...   
6791  hello doctor herpes lip inside mouth third tim...   
6792  hello doctor exploratory nose surgery month ag...   
6793  hi doctor husband trying kid cryptorchidism te...   

                                            answer_text  \
0     hello understand concern issue palpitation pal...   
1     hi thank query following thing might help anxi...   
2     hello understand concern symptom like guilt pr...   
3     hello thank query read query understand concer...   
4     hello understand empathize feel daytoday activ...   
...                                                 ...   
6789  hello need quit habit way try get rid pain gon...   
6790  hello read query understand concern consult op...   
6791  hello understand concern yes look like herpes ...   
6792  hello read query understand concern would like...   
6793  hi undescended testis corrected infancy actual...   

                                                 source                value  
0                                            Cardiology              Anxiety  
1                                            Cardiology              Anxiety  
2                                            Cardiology              Anxiety  
3                                            Cardiology              Anxiety  
4                                            Cardiology              Anxiety  
...                                                 ...                  ...  
6789                                        Endodontist    Clenching Of Jaws  
6790                                          Andrology  Testicle Correction  
6791                                Infectious Diseases     Recurrent Herpes  
6792  Plastic Surgery-reconstructive And Cosmetic Su...          Rhinoplasty  
6793                                  Pediatric Surgery       Cryptorchidism  

[6794 rows x 5 columns]

## Feature Engineering:

In [21]:
# Combine relevant text columns
df_preprocessing['combined_text'] = df_preprocessing['question_description'] + ' ' + df_preprocessing['answer_text']

# Include other features like 'source' and 'value'
features = ['combined_text', 'source', 'value']

# Create a new DataFrame with selected features
df_features = df_preprocessing[features]

# Display the DataFrame with selected features
print(df_features.head())

                                       combined_text      source    value
0  hi doctori 27 year old blood pressure range 11...  Cardiology  Anxiety
1  hi doctor recently experienced choking episode...  Cardiology  Anxiety
2  hi doctoron regular day many problem guilt sha...  Cardiology  Anxiety
3  hello doctor feel severe anxiety overthink lot...  Cardiology  Anxiety
4  hello doctori problem get nervous fast think l...  Cardiology  Anxiety


In [22]:
df_features.sample(5)

combined_text  \
2131  hello doctor sudden acne breakout face includi...   
921   hello doctor girlfriend 19 year old missing pe...   
5629  hi doctor wanted ask possible use upper full d...   
641   hello doctor 32 year old male recently went pr...   
3671  hi doctor girlfriend irritation eye went docto...   

                         source                value  
2131                Dermatology                 Acne  
921   Obstetrics And Gynecology        Missed Period  
5629                  Dentistry        Missing Teeth  
641            General Medicine   Low Platelet Count  
3671                 Pediatrics  Parasitic Infection

In [23]:
corpus =  df_features['combined_text'].tolist()

In [24]:
corpus

['hi doctori 27 year old blood pressure range 11080 mm hg 13071 mm hg pulse rate around 90 beat per minute able feel palpitation left chest stomach feeling coming chest abdomen feeling bit weak today test left hand paining bit please helpthanks hello understand concern issue palpitation palpitation scary especially feel pulse different part body often harmful pose danger especially young people palpitation caused anxiety underlying heart problem etc rarely caused underlying heart disease people age group usually advise patient modify lifestyle must exercise three four time week eat healthy diet sleep seven hour daily avoid smoking caffeine drinking worsen palpitation wish quick recovery hope information help thanks',
 'hi doctor recently experienced choking episode made revert dysphagia severe health anxiety dysphagia last year resulted losing lot weight two month hospitalized week endoscopy barium swallow manometry result showed acid reflux anxiety cause please help want go back losin

In [25]:
input_sequences = []
tokenizer = Tokenizer()
tokenizer.fit_on_texts(corpus)
for line in corpus:
    token_list = tokenizer.texts_to_sequences([line])[0]
    for i in range(1, len(token_list)):
        n_gram_sequence = token_list[:i+1]
        input_sequences.append(n_gram_sequence)


In [26]:
len(input_sequences)

892732

In [27]:
# Enable logging to see the progress of training
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)


In [28]:
# Tokenize the combined text into words
tokenized_text = df_features['combined_text'].apply(word_tokenize)

In [29]:
tokenized_text

0       [hi, doctori, 27, year, old, blood, pressure, ...
1       [hi, doctor, recently, experienced, choking, e...
2       [hi, doctoron, regular, day, many, problem, gu...
3       [hello, doctor, feel, severe, anxiety, overthi...
4       [hello, doctori, problem, get, nervous, fast, ...
                              ...                        
6789    [hi, doctor, clench, jaw, lot, mouth, hurt, qu...
6790    [hello, doctor, 17yearold, male, need, peace, ...
6791    [hello, doctor, herpes, lip, inside, mouth, th...
6792    [hello, doctor, exploratory, nose, surgery, mo...
6793    [hi, doctor, husband, trying, kid, cryptorchid...
Name: combined_text, Length: 6794, dtype: object

In [30]:
# Train Word2Vec model
embedding_size = 100  # You can adjust this based on your requirements
window_size = 5
min_word_count = 1
workers = 4

word2vec_model = Word2Vec(
    sentences=tokenized_text,
    vector_size=embedding_size,
    window=window_size,
    min_count=min_word_count,
    workers=workers
)

# Save the trained Word2Vec model
word2vec_model.save("word2vec_model.model")

# Example: Get the vector representation of a word
vector = word2vec_model.wv['doctor']
print("Vector for 'example_word':", vector)

Vector for 'example_word': [-3.6949751e-01  4.4697821e-01 -2.8923834e-03 -2.3076113e-01
  1.3930538e+00 -1.2881788e+00  1.0878273e+00  2.4027545e+00
  8.9878541e-01 -4.7717422e-01  3.5294062e-01 -2.3245983e+00
 -4.5001662e-01  2.7173817e-01  7.2695750e-01 -1.0169709e+00
  1.0391590e-01  9.2436392e-03 -7.1280330e-01 -8.0822222e-02
  4.8364681e-01 -5.3650522e-01  1.1020241e+00 -1.3388915e+00
  1.0368699e+00  9.5605105e-01 -6.2315154e-01 -1.8403672e-01
  9.9934298e-01 -9.7405985e-02  3.1868765e+00 -1.2482623e+00
  1.9391276e+00 -2.1343794e-01  3.4428361e-01 -3.7973335e-01
  1.9717519e-01 -1.1268215e+00  9.6877009e-01  4.4602584e-02
  1.6163350e+00 -7.5297743e-01 -3.9604086e-01  1.2574427e+00
  6.7627043e-01 -8.4285265e-01 -8.4549427e-01 -1.2691898e+00
 -1.7831257e-02 -3.6602622e-01  8.9203984e-01 -1.1660372e+00
 -7.9863739e-01 -1.2070624e+00 -4.0093350e-01 -1.3700582e-01
  1.9158653e+00  6.0989887e-01  4.8020741e-01  1.8609425e+00
 -1.2192401e+00 -7.4755356e-02  6.2123126e-01 -9.3569964e-

In [32]:
# word2vec_modelzq1

## creating padded sequences.

In [33]:
# input_sequences

In [34]:
# Identify the maximum sequence length in the input sequences
max_sequence_length = max(len(seq) for seq in input_sequences)

In [35]:
max_sequence_length,tokenizer.texts_to_sequences(df_features['combined_text'])

(829,
 [[8,
   205,
   1798,
   13,
   63,
   17,
   131,
   538,
   9051,
   729,
   2530,
   10217,
   729,
   2530,
   1366,
   452,
   119,
   1484,
   1449,
   167,
   128,
   310,
   40,
   931,
   121,
   203,
   168,
   160,
   541,
   203,
   314,
   160,
   549,
   789,
   426,
   15,
   121,
   324,
   2486,
   549,
   14,
   4171,
   3,
   44,
   42,
   86,
   931,
   931,
   4172,
   337,
   40,
   1366,
   375,
   338,
   61,
   419,
   1669,
   3461,
   3389,
   337,
   836,
   323,
   931,
   389,
   116,
   679,
   158,
   30,
   202,
   1479,
   389,
   679,
   158,
   70,
   323,
   143,
   778,
   124,
   222,
   65,
   3922,
   583,
   298,
   89,
   33,
   93,
   11,
   20,
   236,
   192,
   106,
   96,
   243,
   75,
   38,
   54,
   471,
   1670,
   670,
   1596,
   931,
   1094,
   2420,
   1035,
   41,
   182,
   5,
   301],
  [8,
   2,
   289,
   758,
   5885,
   489,
   696,
   612,
   5325,
   149,
   219,
   116,
   5325,
   53,
   13,
   2032,
   1549,
 

In [40]:
# Pad the sequences to have the same length
padded_sequences = pad_sequences(tokenizer.texts_to_sequences(df_features['combined_text']), maxlen=max_sequence_length, padding='pre')


In [41]:
# Display the first few padded sequences
print("First few padded sequences:")
print(padded_sequences[:5])

First few padded sequences:
[[   0    0    0 ...  182    5  301]
 [   0    0    0 ...  144 1770   39]
 [   0    0    0 ... 2570 2033   39]
 [   0    0    0 ...   41  359   39]
 [   0    0    0 ...   41    5   39]]


In [42]:
padded_sequences.size, len(tokenizer.word_index)

(5632226, 24452)

In [43]:
# Define the model
model = Sequential()
model.add(Embedding(input_dim=len(tokenizer.word_index) + 1, output_dim=50, input_length=padded_sequences.shape[1]))
model.add(LSTM(100))
model.add(Dense(units=len(df_features['value'].unique()), activation='softmax'))

# Compile the model
model.compile(optimizer='adam', loss='sparse_categorical_crossentropy', metrics=['accuracy'])

# Display the model summary
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       (None, 829, 50)           1222650   
                                                                 
 lstm (LSTM)                 (None, 100)               60400     
                                                                 
 dense (Dense)               (None, 2505)              253005    
                                                                 
Total params: 1536055 (5.86 MB)
Trainable params: 1536055 (5.86 MB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________


In [44]:
# Extract labels for training
labels = df_features['value'].astype('category').cat.codes.values
labels.size

6794

In [45]:
print("Unique values in labels:", len(df_features['value'].unique()))
print("Length of labels array:", len(labels))

Unique values in labels: 2505
Length of labels array: 6794


In [46]:

# Train the model
model.fit(padded_sequences, labels, epochs=1000, batch_size=32, validation_split=0.2)

Epoch 1/10
170/170 [==============================] - 33s 156ms/step - loss: 7.6262 - accuracy: 0.0063 - val_loss: 9.1274 - val_accuracy: 0.0000e+00
Epoch 2/10
170/170 [==============================] - 19s 114ms/step - loss: 7.2271 - accuracy: 0.0103 - val_loss: 10.0555 - val_accuracy: 0.0000e+00
Epoch 3/10
170/170 [==============================] - 13s 75ms/step - loss: 7.0964 - accuracy: 0.0092 - val_loss: 10.7230 - val_accuracy: 0.0000e+00
Epoch 4/10
170/170 [==============================] - 11s 63ms/step - loss: 6.9422 - accuracy: 0.0094 - val_loss: 11.4756 - val_accuracy: 0.0000e+00
Epoch 5/10
170/170 [==============================] - 11s 65ms/step - loss: 6.7771 - accuracy: 0.0094 - val_loss: 12.2990 - val_accuracy: 0.0000e+00
Epoch 6/10
170/170 [==============================] - 9s 52ms/step - loss: 6.5691 - accuracy: 0.0123 - val_loss: 13.0321 - val_accuracy: 0.0000e+00
Epoch 7/10
170/170 [==============================] - 8s 48ms/step - loss: 6.3383 - accuracy: 0.0177 - val